In [1]:
import folium
import pandas as pd
import os
import re

# Load the data
df = pd.read_csv('~/Documents/SOCY3001/SOCY3001/output.csv')

pattern = r'^-?\d+(\.\d+)?, -?\d+(\.\d+)?$'
df.iloc[:, 3] = df.iloc[:, 3].apply(lambda x: x if re.match(pattern, x) else "Not specified")
df = df[df['Coordinates'] != 'Not specified']

# Create a base map with a custom tile layer
m = folium.Map(location=[20, 0], zoom_start=2, tiles='CartoDB positron')

# Define a soft and high-contrast color palette for categories
colors = {
    'Forest fire monitoring and prevention': '#B57EDC',  # Soft lavender
    'Tree species classification': '#FF69B4',  # Rich Pink
    'Forest cover assessment': '#77B5FE',  # Sky Blue
    'Canopy and biomass estimation': '#9DC183',  # Sage Green
    'Habitat degradation and biodiversity monitoring': '#FFC87C',  # Soft Gold
    'Other': '#A3A3A3'  # Soft Slate Grey
}

# Add points to the map with styled popups
for i, row in df.iterrows():
    latitude, longitude = map(float, row['Coordinates'].split(', '))
    popup_html = f"""
    <div style="font-family: Arial; font-size: 14px;">
        <b>{row['Title']}</b><br>
        <i>Category:</i> {row['Category']}<br>
        <i>Location:</i> {row['Location']}
    </div>
    """
    
    folium.CircleMarker(
        location=(latitude, longitude),
        color=colors.get(row['Category'], 'black'),
        fill=True,
        fill_color=colors.get(row['Category'], 'black'),
        radius=3,
        fill_opacity=0.7,  # Slight transparency for a softer look
        weight=0,
        popup=folium.Popup(popup_html, max_width=250)
    ).add_to(m)

# Add an enhanced legend
legend_html = '''
<div style="position: fixed; 
            bottom: 50px; left: 50px; width: 300px; height: 170px; 
            border:2px solid grey; z-index:9999; font-size:14px;
            background-color:white; padding: 10px; box-shadow: 3px 3px 6px rgba(0,0,0,0.3); border-radius: 5px;">
    <b>Category Legend</b><br>
    <i class="fa fa-circle fa-1x" style="color:#B57EDC"></i> Forest fire monitoring and prevention <br>
    <i class="fa fa-circle fa-1x" style="color:#FF69B4"></i> Tree species classification <br>
    <i class="fa fa-circle fa-1x" style="color:#77B5FE"></i> Forest cover assessment <br>
    <i class="fa fa-circle fa-1x" style="color:#9DC183"></i> Canopy and biomass estimation <br>
    <i class="fa fa-circle fa-1x" style="color:#FFC87C"></i> Habitat and biodiversity monitoring <br>
    <i class="fa fa-circle fa-1x" style="color:#A3A3A3"></i> Other
</div>
'''
m.get_root().html.add_child(folium.Element(legend_html))

# Save or display the map
file_path = os.path.expanduser('~/Documents/SOCY3001/ResearchMapping/map.html')
m.save(file_path)
m